# Setting up a user environment

Topics
* Setup a user environment [using conda](#using-conda)
    - [Add user environment to notebook kernels](#add-the-new-environment-to-your-active-kernels)
    - [Activate your conda environment](#activate-your-conda-environment)
* Setup a user environment [using venv](#using-virtual-environment)
* Include `PATH` in [Notebook Kernel](#add-path-to-your-user-environment)


In [1]:
!module list

Currently Loaded Modulefiles:
 1) miniconda3/4.8.2-gcc-8.3.1-3m7b6t2  
>

## Using conda

In [2]:
!conda info


     active environment : None
       user config file : /jetfs/home/mblaschek/.condarc
 populated config files : /jetfs/home/mblaschek/.condarc
          conda version : 4.8.5
    conda-build version : not installed
         python version : 3.8.1.final.0
       virtual packages : __glibc=2.28
       base environment : /jetfs/spack/opt/spack/linux-rhel8-skylake_avx512/gcc-8.3.1/miniconda3-4.8.2-3m7b6t2kgedyr3jnd2nasmgiq7wm27iv  (read only)
           channel URLs : https://repo.anaconda.com/pkgs/main/linux-64
                          https://repo.anaconda.com/pkgs/main/noarch
                          https://repo.anaconda.com/pkgs/r/linux-64
                          https://repo.anaconda.com/pkgs/r/noarch
          package cache : /jetfs/spack/opt/spack/linux-rhel8-skylake_avx512/gcc-8.3.1/miniconda3-4.8.2-3m7b6t2kgedyr3jnd2nasmgiq7wm27iv/pkgs
                          /jetfs/home/mblaschek/.conda/pkgs
       envs directories : /jetfs/home/mblaschek/.conda/envs
                   

In [3]:
# Create a environment with conda
!conda create -y -n myenv python=3.7 numpy ipykernel

Solving environment: failed with repodata from current_repodata.json, will retry with next repodata source.
Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.5
  latest version: 4.9.2

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /jetfs/home/mblaschek/.conda/envs/myenv

  added / updated specs:
    - ipykernel
    - numpy
    - python=3.7


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2020.11.8          |   py37h06a4308_0         148 KB
    ipython-7.19.0             |   py37hb070fc8_0         978 KB
    jupyter_core-4.7.0         |   py37h06a4308_0          68 KB
    numpy-1.19.2               |   py37h54aff64_0          22 KB
    numpy-base-1.19.2          |   py37hfa32c7d_0         4.1 MB
    pexpect-4.8.0              |     pyhd3eb1b0_3         

### Add the new environment to your active kernels
This way you can choose the kernel from the Jupyterlab launcher.

In [4]:
!~/.conda/envs/myenv/bin/python -m ipykernel install --user --name MYENV --display-name "Py3.7"

Installed kernelspec MYENV in /jetfs/home/mblaschek/.local/share/jupyter/kernels/myenv


### Activate your conda environment
Conda Environments need to be added to the `PATH` to work well. So there is an `activate` function for these conda environments.

However, running
```bash
conda init bash
```
will edit your `.bashrc` and that is not nice, especially when you might move to another module. 
**Therefore this is not recommended to do.**

This script is used by `conda init bash` to set the configuration, we simply source (load) it and get the same functionality as we would be using `conda init bash`. 

**(Do not use `conda init bash`)**


```bash
# source the conda functionality
eval "$(conda shell.bash hook)"
# or
source $(dirname $(which conda))/../etc/profile.d/conda.sh
# now activating the environment works
conda activate myenv
```

#### bash conda_activate function
optionally you can add this bash function to your `.bashrc` for convenience:

```bash
conda_activate(){
    if ! command -v conda &> /dev/null; then
        echo "Load ana/miniconda module first"
    else
        if [ $# -ne 1 ]; then
            echo "usage: conda_activate [env-name]"
            
        else
            source $(dirname $(which conda))/../etc/profile.d/conda.sh
            conda activate $1
        fi
    fi
}
```
Source your bashrc by running: `source ~/.bashrc` or logout/login again. Then you should be able to use the function:

```bash
module load anaconda3
conda_activate myenv
```

In [5]:
# List available Kernels
!jupyter kernelspec list

Available kernels:
  myenv      /jetfs/home/mblaschek/.local/share/jupyter/kernels/myenv
  python3    /jetfs/spack/opt/spack/linux-rhel8-skylake_avx512/gcc-8.3.1/miniconda3-4.8.2-3m7b6t2kgedyr3jnd2nasmgiq7wm27iv/share/jupyter/kernels/python3


## Using virtual environment

In [6]:
# Setup a virtual Environment for your Python in the directoy: myfancyenv
!python -m venv myfancyenv 

In [7]:
# Creates a directory with new environment
!ls myfancyenv/

bin  include  lib  lib64  pyvenv.cfg


In [8]:
# Install some package into that environment
# important is ipykernel to use it within jupyterlab/notebook
!./myfancyenv/bin/pip -q install numpy scipy pandas ipykernel

You should consider upgrading via the 'pip install --upgrade pip' command.


In [9]:
# Allow this environment to be available on the LAUNCHERS (+) sign on the left
!./myfancyenv/bin/python -m ipykernel install --user --name fancy --display-name "My Python"

Installed kernelspec fancy in /jetfs/home/mblaschek/.local/share/jupyter/kernels/fancy


Wait a bit and the new python environment should be available on your launchers.

In [10]:
!jupyter kernelspec list

Available kernels:
  fancy      /jetfs/home/mblaschek/.local/share/jupyter/kernels/fancy
  myenv      /jetfs/home/mblaschek/.local/share/jupyter/kernels/myenv
  python3    /jetfs/spack/opt/spack/linux-rhel8-skylake_avx512/gcc-8.3.1/miniconda3-4.8.2-3m7b6t2kgedyr3jnd2nasmgiq7wm27iv/share/jupyter/kernels/python3


## Add PATH to your user environment

In order to get full access to all tools installed in your local environment, add it to your `PATH`.

Open your `kernel.json` file located `/jetfs/home/mblaschek/.local/share/jupyter/kernels/myenv/kernel.json`:
```json
{
    "argv": [
        "/jetfs/home/mblaschek/.conda/envs/myenv/bin/python",
        "-m",
        "ipykernel_launcher",
        "-f",
        "{connection_file}"
    ],
    "env" : {
        "PATH": "/jetfs/home/mblaschek/.conda/envs/myenv/bin/:${PATH}",
        "LD_LIBRARY_PATH": "/jetfs/home/mblaschek/.conda/envs/myenv/lib:${LD_LIBRARY_PATH}"
    },
    "display_name": "MYENV",
    "language": "python"
}
```

### Finished